In [1]:
# Load model directly
from transformers import AutoImageProcessor, AutoModelForImageClassification

processor = AutoImageProcessor.from_pretrained("shahukareem/coral-classification")
model = AutoModelForImageClassification.from_pretrained("shahukareem/coral-classification")

2024-08-18 14:20:46.889006: E external/local_xla/xla/stream_executor/cuda/cuda_fft.cc:485] Unable to register cuFFT factory: Attempting to register factory for plugin cuFFT when one has already been registered
2024-08-18 14:20:46.916613: E external/local_xla/xla/stream_executor/cuda/cuda_dnn.cc:8454] Unable to register cuDNN factory: Attempting to register factory for plugin cuDNN when one has already been registered
2024-08-18 14:20:46.925904: E external/local_xla/xla/stream_executor/cuda/cuda_blas.cc:1452] Unable to register cuBLAS factory: Attempting to register factory for plugin cuBLAS when one has already been registered
2024-08-18 14:20:46.948751: I tensorflow/core/platform/cpu_feature_guard.cc:210] This TensorFlow binary is optimized to use available CPU instructions in performance-critical operations.
To enable the following instructions: AVX2 FMA, in other operations, rebuild TensorFlow with the appropriate compiler flags.
2024-08-18 14:20:49.247897: W tensorflow/compiler/tf2

In [2]:
from datasets import load_dataset

# Load dataset (contoh menggunakan CIFAR-10)
dataset = load_dataset("cifar10")
train_dataset = dataset["train"]
test_dataset = dataset["test"]


In [3]:
print(train_dataset.column_names)
print(test_dataset.column_names)
import PIL
print(PIL.__version__)


['img', 'label']
['img', 'label']
10.4.0


In [4]:
import PIL
print(PIL.__version__)


10.4.0


In [5]:
from PIL import Image, ExifTags

def preprocess_function(examples):
    print(f"Processing examples: {examples['img']}")
    return processor(examples['img'], return_tensors="pt")

train_dataset = train_dataset.map(preprocess_function, batched=True, load_from_cache_file=False)
test_dataset = test_dataset.map(preprocess_function, batched=True, load_from_cache_file=False)


Map:   0%|          | 0/50000 [00:00<?, ? examples/s]

Processing examples: [<PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E0618A30>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E06189D0>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A0EB0>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A1240>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A1BD0>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2560>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A25C0>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2620>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2680>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A26E0>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2740>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A27A0>, <PIL.PngImagePlugin.PngImageFi

Map:   0%|          | 0/10000 [00:00<?, ? examples/s]

Processing examples: [<PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A3FA0>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A3F70>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A0EB0>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2770>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2890>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A28F0>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2D40>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2C20>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2A40>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2C80>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2740>, <PIL.PngImagePlugin.PngImageFile image mode=RGB size=32x32 at 0x7FC8E04A2FB0>, <PIL.PngImagePlugin.PngImageFi

In [7]:
from transformers import Trainer, TrainingArguments

training_args = TrainingArguments(
    output_dir="./results",
    evaluation_strategy="epoch",
    per_device_train_batch_size=8,
    per_device_eval_batch_size=8,
    num_train_epochs=3,
    save_strategy="epoch",
    save_total_limit=2,
    load_best_model_at_end=True,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=train_dataset,
    eval_dataset=test_dataset,
    tokenizer=processor,
)

trainer.train()


/home/anugerahsurya/.local/lib/python3.10/site-packages/transformers/training_args.py:1525: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(


RuntimeError: CUDA error: device-side assert triggered
CUDA kernel errors might be asynchronously reported at some other API call, so the stacktrace below might be incorrect.
For debugging consider passing CUDA_LAUNCH_BLOCKING=1.
Compile with `TORCH_USE_CUDA_DSA` to enable device-side assertions.


In [ ]:
model.save_pretrained("./fine_tuned_model")
processor.save_pretrained("./fine_tuned_processor")
